<b>This notebook is just a tutorial for you to get familiar with skip-gram and MapReduce.  
<font color="red">You don't need to hand in this notebook</font>, so feel free to jump to [Requirement section](#Assignment-Requirement) and directly work on your `mapper.py` and `reducer.py` if you already have the idea of how to do so.</b>  

# Week 05: Skip-gram and MapReduce

In previous assignments, you have known the concept of ngrams and how to generate them.  
This week, we are introducing another gram type, called *skip-gram*, to you.  
Also, we are going to calculate it on a large dataset, so you'll have to process it with the MapReduce technique.  

So, first thing first: what is skip-gram?  

## Skip-gram

<i>\[S\]kip-grams are a generalization of n-grams in which the components (typically words) need not be consecutive in the text under consideration, but may leave gaps that are skipped over.  - from [Wikipedia](https://en.wikipedia.org/wiki/N-gram#Skip-gram)</i>  

That is, skip-gram is actually the same as ngram, but allowed to skip some words in between.  
In the sentence <i>"Strong winds blew roofs away"</i>, two of its bigrams are <i>"winds blew"</i> and <i>"blew roofs"</i>, while <i>"blew away"</i> is one of the skipgrams with distance 2, since it skipped one word <i>"roofs"</i> .  
As you can see, skipgram is able to capture the phrase seperated by other words.  

Now consider another sentence

> "Skip-gram is used to predict the context word for a given target word".

With a pivot word *predict*, all of its skip-grams within distance 5 are as below:
```
.------------------------------------------------------------------------------.
| distance || -5 |     -4    | -3 |  -2  | -1 |  1  |    2    |  3   |  4  | 5 |
|----------||----|-----------|----|------|----|-----|---------|------|-----|---|
| predict  || -  | Skip-gram | is | used | to | the | context | word | for | a |
'------------------------------------------------------------------------------'
```

<a name="Practice"></a>
### Practice: Distance table of skip-gram

Now, let's practice!  
Given a sentence <i>"Skip-gram is used to predict the context word for a given target word"</i>, <u>**output all of its skip-gram with distance between -3 to 3</u> and show the result in a table**.  

**Example**
```
distance      -3            -2            -1            1             2             3             
--------------------------------------------------------------------------------------------
Skip-gram     -             -             -             is            used          to            
is            -             -             Skip-gram     used          to            predict       
used          -             Skip-gram     is            to            predict       the           
to            Skip-gram     is            used          predict       the           context       
predict       is            used          to            the           context       word          
the           used          to            predict       context       word          for           
context       to            predict       the           word          for           a             
word          predict       the           context       for           a             given         
for           the           context       word          a             given         target        
a             context       word          for           given         target        word          
given         word          for           a             target        word          -             
target        for           a             given         word          -             -             
word          a             given         target        -             -             -             
```

\*Hint: Try to get the skip-grams for a single word first if you have trouble generating them all at once. 
```
(predict, is, -3)
(predict, used, -2)
(predict, to, -1)
(predict, the, 1)
(predict, context, 2)
(predict, word, 3)
```

In [1]:
tokens = "Skip-gram is used to predict the context word for a given target word".split()
token_length = len(tokens)

for idx in range(token_length):
    ...

distance      -3            -2            -1            1             2             3             
--------------------------------------------------------------------------------------------
Skip-gram     -             -             -             is            used          to            
is            -             -             Skip-gram     used          to            predict       
used          -             Skip-gram     is            to            predict       the           
to            Skip-gram     is            used          predict       the           context       
predict       is            used          to            the           context       word          
the           used          to            predict       context       word          for           
context       to            predict       the           word          for           a             
word          predict       the           context       for           a             given         
for           th

## MapReduce

<i>MapReduce is a programming model and an associated implementation for processing and generating big data sets with a parallel, distributed algorithm on a cluster. - from [Wikipedia](https://en.wikipedia.org/wiki/MapReduce)</i> 

### Why MapReduce?

Imagine that you are working on a pretty large dataset, say all pages on Wikipedia (whose size has already reached 94GB in 2013).  
Most likely you are not able to process the whole corpus in the memory or on a single computer. Even a simple frequency counter would be challenging under such a huge data size.  
To deal with this, Google proposed a big-data processing model called MapReduce, and it has been implemented and supported by many distributed computing systems, such as Apache Hadoop.  
The core concept of MapReduce is to **split, apply and then combine**, so that each data segment can be handled separately.  

### Mapper-Shuffler-Reducer

![](https://www.todaysoftmag.com/images/articles/tsm33/large/a11.png)
<small><i> - image source: [Today Software Magazine](https://www.todaysoftmag.com/article/1358/hadoop-mapreduce-deep-diving-and-tuning)</i></small> 

As you can see in the picture:  
First, the whole data is split into some smaller partitions, each partition able to be processed by an independant machine.  
In this step, **mappers** will generate one or more key-value pair(s) that can easily be clustered.  
 - example: in a word counter, it would generate the word and the word's current count.  

Then, we will **shuffle** and group all outputs from mappers.  
 - example: sort the output from mappers.  

Lastly, we can combine the grouped values and **reduce** them into final results.  
 - example: calculate total frequency in each group.  

## MapReduce for skip-gram

Now, having the concepts of skip-gram and MapReduce in mind, it's time to put these all together: let's generate skip-gram table with MapReduce technique!  

It may sound scary to some of you, so let's break it down first.  
There are 3 steps to do, and each step is described as below:
1. **Mapper**: Print all skip-gram with its distance infomation, and the current count of it.  
   ```
   a b -3 1
   a c 3  1
   c e -2 1
   a c 1  1
   a b -3 1
   b d 2  1
   ```
2. **Shuffler**: Group all skipgrams by its text. This can be easily achieved with sorting.  
   ```
   a b -3 1
   a b -3 1
   a c 1  1
   a c 3  1
   b d 2  1
   c e -2 1
   ```
3. **Reducer** :  
   Since the results have been sorted in the previous step, we can easily calculate the frequency of each skip-gram with different distance.  
   So we can know that the frequency of skipgram `a b` with distance $-3$ should be $1+1=2$, while other skip-grams' are all $1$.

### Step 1: Mapper

First, in the mapper we want to generate all skip-grams within distance $-5$ to $5$.  
Remember that you've already done something similar in [previous Practice](#Practice)? Just modify it to MapReduce format!  

Output: 
 - `"{pivot}\t{word}\t{distance}\t{count}"`  

Example: 
```
predict is  -3  1
predict used    -2  1
predict the -1  1
predict the 1   1
...
```



In [2]:
import os

In [3]:
with open(os.path.join('data', 'wiki1G.txt')) as f:
    for line in f:
        ...
        break # for the sake of this practice, just test the first page now

anarchism	anarchism	1	1
anarchism	is	2	1
anarchism	a	3	1
anarchism	political	4	1
anarchism	philosophy	5	1
anarchism	anarchism	-1	1
anarchism	is	1	1
anarchism	a	2	1
anarchism	political	3	1
anarchism	philosophy	4	1
anarchism	and	5	1
is	anarchism	-2	1
is	anarchism	-1	1
is	a	1	1
is	political	2	1
is	philosophy	3	1
is	and	4	1
is	movement	5	1
a	anarchism	-3	1
a	anarchism	-2	1
a	is	-1	1
a	political	1	1
a	philosophy	2	1
a	and	3	1
a	movement	4	1
a	that	5	1
political	anarchism	-4	1
political	anarchism	-3	1
political	is	-2	1
political	a	-1	1
political	philosophy	1	1
political	and	2	1
political	movement	3	1
political	that	4	1
political	is	5	1
philosophy	anarchism	-5	1
philosophy	anarchism	-4	1
philosophy	is	-3	1
philosophy	a	-2	1
philosophy	political	-1	1
philosophy	and	1	1
philosophy	movement	2	1
philosophy	that	3	1
philosophy	is	4	1
philosophy	sceptical	5	1
and	anarchism	-5	1
and	is	-4	1
and	a	-3	1
and	political	-2	1
and	philosophy	-1	1
and	movement	1	1
and	that	2	1
and	is	3	1
and	sceptical	4	1
a

anarchism	criticism	-2	1
anarchism	of	-1	1
anarchism	mainly	1	1
anarchism	focuses	2	1
anarchism	on	3	1
anarchism	claims	4	1
anarchism	of	5	1
mainly	human	-5	1
mainly	society	-4	1
mainly	criticism	-3	1
mainly	of	-2	1
mainly	anarchism	-1	1
mainly	focuses	1	1
mainly	on	2	1
mainly	claims	3	1
mainly	of	4	1
mainly	it	5	1
focuses	society	-5	1
focuses	criticism	-4	1
focuses	of	-3	1
focuses	anarchism	-2	1
focuses	mainly	-1	1
focuses	on	1	1
focuses	claims	2	1
focuses	of	3	1
focuses	it	4	1
focuses	being	5	1
on	criticism	-5	1
on	of	-4	1
on	anarchism	-3	1
on	mainly	-2	1
on	focuses	-1	1
on	claims	1	1
on	of	2	1
on	it	3	1
on	being	4	1
on	internally	5	1
claims	of	-5	1
claims	anarchism	-4	1
claims	mainly	-3	1
claims	focuses	-2	1
claims	on	-1	1
claims	of	1	1
claims	it	2	1
claims	being	3	1
claims	internally	4	1
claims	inconsistent	5	1
of	anarchism	-5	1
of	mainly	-4	1
of	focuses	-3	1
of	on	-2	1
of	claims	-1	1
of	it	1	1
of	being	2	1
of	internally	3	1
of	inconsistent	4	1
of	violent	5	1
it	mainly	-5	1
it	focu

associate	do	-2	1
associate	not	-1	1
associate	themselves	1	1
associate	with	2	1
associate	authoritarian	3	1
associate	socialists	4	1
associate	or	5	1
themselves	marxists	-5	1
themselves	who	-4	1
themselves	do	-3	1
themselves	not	-2	1
themselves	associate	-1	1
themselves	with	1	1
themselves	authoritarian	2	1
themselves	socialists	3	1
themselves	or	4	1
themselves	a	5	1
with	who	-5	1
with	do	-4	1
with	not	-3	1
with	associate	-2	1
with	themselves	-1	1
with	authoritarian	1	1
with	socialists	2	1
with	or	3	1
with	a	4	1
with	vanguard	5	1
authoritarian	do	-5	1
authoritarian	not	-4	1
authoritarian	associate	-3	1
authoritarian	themselves	-2	1
authoritarian	with	-1	1
authoritarian	socialists	1	1
authoritarian	or	2	1
authoritarian	a	3	1
authoritarian	vanguard	4	1
authoritarian	party	5	1
socialists	not	-5	1
socialists	associate	-4	1
socialists	themselves	-3	1
socialists	with	-2	1
socialists	authoritarian	-1	1
socialists	or	1	1
socialists	a	2	1
socialists	vanguard	3	1
socialists	party	4	1
socialists

suggestion	coercive	-4	1
suggestion	society	-3	1
suggestion	and	-2	1
suggestion	a	-1	1
suggestion	on	1	1
suggestion	how	2	1
suggestion	to	3	1
suggestion	act	4	1
suggestion	to	5	1
on	coercive	-5	1
on	society	-4	1
on	and	-3	1
on	a	-2	1
on	suggestion	-1	1
on	how	1	1
on	to	2	1
on	act	3	1
on	to	4	1
on	pursue	5	1
how	society	-5	1
how	and	-4	1
how	a	-3	1
how	suggestion	-2	1
how	on	-1	1
how	to	1	1
how	act	2	1
how	to	3	1
how	pursue	4	1
how	the	5	1
to	and	-5	1
to	a	-4	1
to	suggestion	-3	1
to	on	-2	1
to	how	-1	1
to	act	1	1
to	to	2	1
to	pursue	3	1
to	the	4	1
to	ideal	5	1
act	a	-5	1
act	suggestion	-4	1
act	on	-3	1
act	how	-2	1
act	to	-1	1
act	to	1	1
act	pursue	2	1
act	the	3	1
act	ideal	4	1
act	of	5	1
to	suggestion	-5	1
to	on	-4	1
to	how	-3	1
to	to	-2	1
to	act	-1	1
to	pursue	1	1
to	the	2	1
to	ideal	3	1
to	of	4	1
to	anarchy	5	1
pursue	on	-5	1
pursue	how	-4	1
pursue	to	-3	1
pursue	act	-2	1
pursue	to	-1	1
pursue	the	1	1
pursue	ideal	2	1
pursue	of	3	1
pursue	anarchy	4	1
pursue	herbert	5	1
the	how	-5	1
t

most	as	-3	1
most	a	-2	1
most	reaction	-1	1
most	notable	1	1
most	precursors	2	1
most	to	3	1
most	anarchism	4	1
most	in	5	1
notable	espoused	-5	1
notable	as	-4	1
notable	a	-3	1
notable	reaction	-2	1
notable	most	-1	1
notable	precursors	1	1
notable	to	2	1
notable	anarchism	3	1
notable	in	4	1
notable	the	5	1
precursors	as	-5	1
precursors	a	-4	1
precursors	reaction	-3	1
precursors	most	-2	1
precursors	notable	-1	1
precursors	to	1	1
precursors	anarchism	2	1
precursors	in	3	1
precursors	the	4	1
precursors	ancient	5	1
to	a	-5	1
to	reaction	-4	1
to	most	-3	1
to	notable	-2	1
to	precursors	-1	1
to	anarchism	1	1
to	in	2	1
to	the	3	1
to	ancient	4	1
to	world	5	1
anarchism	reaction	-5	1
anarchism	most	-4	1
anarchism	notable	-3	1
anarchism	precursors	-2	1
anarchism	to	-1	1
anarchism	in	1	1
anarchism	the	2	1
anarchism	ancient	3	1
anarchism	world	4	1
anarchism	were	5	1
in	most	-5	1
in	notable	-4	1
in	precursors	-3	1
in	to	-2	1
in	anarchism	-1	1
in	the	1	1
in	ancient	2	1
in	world	3	1
in	were	4	1
in	in	

...

for	need	-1	1
for	a	1	1
for	system	2	1
for	that	3	1
for	focuses	4	1
for	on	5	1
a	focusing	-5	1
a	on	-4	1
a	the	-3	1
a	need	-2	1
a	for	-1	1
a	system	1	1
a	that	2	1
a	focuses	3	1
a	on	4	1
a	children	5	1
system	on	-5	1
system	the	-4	1
system	need	-3	1
system	for	-2	1
system	a	-1	1
system	that	1	1
system	focuses	2	1
system	on	3	1
system	children	4	1
system	s	5	1
that	the	-5	1
that	need	-4	1
that	for	-3	1
that	a	-2	1
that	system	-1	1
that	focuses	1	1
that	on	2	1
that	children	3	1
that	s	4	1
that	creativity	5	1
focuses	need	-5	1
focuses	for	-4	1
focuses	a	-3	1
focuses	system	-2	1
focuses	that	-1	1
focuses	on	1	1
focuses	children	2	1
focuses	s	3	1
focuses	creativity	4	1
focuses	rather	5	1
on	for	-5	1
on	a	-4	1
on	system	-3	1
on	that	-2	1
on	focuses	-1	1
on	children	1	1
on	s	2	1
on	creativity	3	1
on	rather	4	1
on	than	5	1
children	a	-5	1
children	system	-4	1
children	that	-3	1
children	focuses	-2	1
children	on	-1	1
children	s	1	1
children	creativity	2	1
children	rather	3	1
children	than	4	1
ch

domination	coercion	-1	1
domination	by	1	1
domination	means	2	1
domination	of	3	1
domination	coercion	4	1
domination	camouflaged	5	1
by	state	-5	1
by	as	-4	1
by	meaning	-3	1
by	coercion	-2	1
by	domination	-1	1
by	means	1	1
by	of	2	1
by	coercion	3	1
by	camouflaged	4	1
by	if	5	1
means	as	-5	1
means	meaning	-4	1
means	coercion	-3	1
means	domination	-2	1
means	by	-1	1
means	of	1	1
means	coercion	2	1
means	camouflaged	3	1
means	if	4	1
means	possible	5	1
of	meaning	-5	1
of	coercion	-4	1
of	domination	-3	1
of	by	-2	1
of	means	-1	1
of	coercion	1	1
of	camouflaged	2	1
of	if	3	1
of	possible	4	1
of	but	5	1
coercion	coercion	-5	1
coercion	domination	-4	1
coercion	by	-3	1
coercion	means	-2	1
coercion	of	-1	1
coercion	camouflaged	1	1
coercion	if	2	1
coercion	possible	3	1
coercion	but	4	1
coercion	unceremonious	5	1
camouflaged	domination	-5	1
camouflaged	by	-4	1
camouflaged	means	-3	1
camouflaged	of	-2	1
camouflaged	coercion	-1	1
camouflaged	if	1	1
camouflaged	possible	2	1
camouflaged	but	3	1
camoufla

ecological	had	-2	1
ecological	an	-1	1
ecological	aesthetic	1	1
ecological	and	2	1
ecological	offered	3	1
ecological	an	4	1
ecological	example	5	1
aesthetic	impressionist	-5	1
aesthetic	movement	-4	1
aesthetic	had	-3	1
aesthetic	an	-2	1
aesthetic	ecological	-1	1
aesthetic	and	1	1
aesthetic	offered	2	1
aesthetic	an	3	1
aesthetic	example	4	1
aesthetic	of	5	1
and	movement	-5	1
and	had	-4	1
and	an	-3	1
and	ecological	-2	1
and	aesthetic	-1	1
and	offered	1	1
and	an	2	1
and	example	3	1
and	of	4	1
and	an	5	1
offered	had	-5	1
offered	an	-4	1
offered	ecological	-3	1
offered	aesthetic	-2	1
offered	and	-1	1
offered	an	1	1
offered	example	2	1
offered	of	3	1
offered	an	4	1
offered	anarchist	5	1
an	an	-5	1
an	ecological	-4	1
an	aesthetic	-3	1
an	and	-2	1
an	offered	-1	1
an	example	1	1
an	of	2	1
an	an	3	1
an	anarchist	4	1
an	perception	5	1
example	ecological	-5	1
example	aesthetic	-4	1
example	and	-3	1
example	offered	-2	1
example	an	-1	1
example	of	1	1
example	an	2	1
example	anarchist	3	1
example	per

of	philosophical	-2	1
of	anarchism	-1	1
of	being	1	1
of	ineffective	2	1
of	all	3	1
of	talk	4	1
of	and	5	1
being	critique	-5	1
being	towards	-4	1
being	philosophical	-3	1
being	anarchism	-2	1
being	of	-1	1
being	ineffective	1	1
being	all	2	1
being	talk	3	1
being	and	4	1
being	thoughts	5	1
ineffective	towards	-5	1
ineffective	philosophical	-4	1
ineffective	anarchism	-3	1
ineffective	of	-2	1
ineffective	being	-1	1
ineffective	all	1	1
ineffective	talk	2	1
ineffective	and	3	1
ineffective	thoughts	4	1
ineffective	and	5	1
all	philosophical	-5	1
all	anarchism	-4	1
all	of	-3	1
all	being	-2	1
all	ineffective	-1	1
all	talk	1	1
all	and	2	1
all	thoughts	3	1
all	and	4	1
all	in	5	1
talk	anarchism	-5	1
talk	of	-4	1
talk	being	-3	1
talk	ineffective	-2	1
talk	all	-1	1
talk	and	1	1
talk	thoughts	2	1
talk	and	3	1
talk	in	4	1
talk	the	5	1
and	of	-5	1
and	being	-4	1
and	ineffective	-3	1
and	all	-2	1
and	talk	-1	1
and	thoughts	1	1
and	and	2	1
and	in	3	1
and	the	4	1
and	meantime	5	1
thoughts	being	-5	1
though

has	is	-3	1
has	that	-2	1
has	it	-1	1
has	a	1	1
has	utopian	2	1
has	character	3	1
has	because	4	1
has	all	5	1
a	anarchism	-5	1
a	is	-4	1
a	that	-3	1
a	it	-2	1
a	has	-1	1
a	utopian	1	1
a	character	2	1
a	because	3	1
a	all	4	1
a	individuals	5	1
utopian	is	-5	1
utopian	that	-4	1
utopian	it	-3	1
utopian	has	-2	1
utopian	a	-1	1
utopian	character	1	1
utopian	because	2	1
utopian	all	3	1
utopian	individuals	4	1
utopian	should	5	1
character	that	-5	1
character	it	-4	1
character	has	-3	1
character	a	-2	1
character	utopian	-1	1
character	because	1	1
character	all	2	1
character	individuals	3	1
character	should	4	1
character	have	5	1
because	it	-5	1
because	has	-4	1
because	a	-3	1
because	utopian	-2	1
because	character	-1	1
because	all	1	1
because	individuals	2	1
because	should	3	1
because	have	4	1
because	anarchist	5	1
all	has	-5	1
all	a	-4	1
all	utopian	-3	1
all	character	-2	1
all	because	-1	1
all	individuals	1	1
all	should	2	1
all	have	3	1
all	anarchist	4	1
all	views	5	1
individuals	a	-5	1
indivi

### Step 2: Shuffler

All we need to do in the shuffler is sorting, so let's use the built-in command to do this for us!  

Try this on your terminal/command prompt ;)  
(You can get the sample input from [here](https://drive.google.com/drive/folders/1vKxr--sLd2J4kdsXUzJDBZdG3AmV4NGl?usp=sharing))

**Unix**  
```bash
sort -k1,3 < mapper.sample.tsv
```
**Windows**
```powershell
type mapper.sample.tsv | sort
```

### Step 3: Reducer

Since all the input should have been sorted in previous shuffler, the task of reducer is pretty simple: just count how many times the same gram appears, and then print the count out!

Input: 
 - `"{pivot}\t{word}\t{distance}\t{count}"`
 - You can get a sample input file `shuffler.sample.tsv` from [here](https://drive.google.com/drive/folders/1vKxr--sLd2J4kdsXUzJDBZdG3AmV4NGl?usp=sharing)

Output: 
 - `"{pivot}\t{word}\t{total_freq}\t{-5}\t{-4}\t{-3}\t{-2}\t{-1}\t{1}\t{2}\t{3}\t{4}\t{5}"`
 - The first two column are the skipgram; the third column is the sum of total frequency; column 4\~13 are the frequency with distance -5\~5, without 0.

Example:
 - `arouse  open    4       0       0       3       0       0       0       0       0       0       1`

Hints: 
1. Parse the input from shuffler
2. Check if this is the same skipgram as the previous one
3. If so, add the frequency according to its distance
4. If not, output the previous skipgram data

Note that you may NOT want to store all your counting results in a dict or any data structure.  
Recall that one purpose of MapReduce is to prevent memory exhaustion. It loses its value if you end up storing it again.  
Instead, <u>directly print it out or write it into a file</u> .  
(Don't get me wrong: of course you can store some temporary data, but let's not store the whole result and then print it out at once, okay?)


In [4]:
with open(os.path.join('data', 'shuffler.sample.tsv')) as f:
    
    for line in f:
        # 1) Parse the input from shuffler
        # 2) Check if this is the same skipgram
        # 3) If so, add the frequency according to its distance
        # 4) If not, output the previous skipgram data
        
        ...

1539	a	1	0	0	0	0	0	0	0	0	0	1
1539	anarchisme	1	0	1	0	0	0	0	0	0	0	0
1539	anarchy	1	0	0	0	1	0	0	0	0	0	0
1539	and	1	0	0	1	0	0	0	0	0	0	0
1539	as	1	1	0	0	0	0	0	0	0	0	0
1539	early	1	0	0	0	0	0	1	0	0	0	0
1539	empahised	1	0	0	0	0	0	0	0	0	1	0
1539	english	1	0	0	0	0	0	0	1	0	0	0
1539	from	1	0	0	0	0	1	0	0	0	0	0
1539	usages	1	0	0	0	0	0	0	0	1	0	0
1642	anarchism	1	1	0	0	0	0	0	0	0	0	0
1642	anarchisme	1	0	0	0	0	0	0	1	0	0	0
1642	anarchy	1	0	0	0	0	0	0	0	0	1	0
1642	and	1	0	0	0	0	0	0	0	1	0	0
1642	appears	1	0	1	0	0	0	0	0	0	0	0
1642	as	1	0	0	0	0	0	1	0	0	0	0
1642	english	1	0	0	0	1	0	0	0	0	0	0
1642	from	2	0	0	0	0	1	0	0	0	0	1
1642	in	1	0	0	1	0	0	0	0	0	0	0
1756	1808	1	0	0	0	0	0	0	0	0	0	1
1756	1836	1	0	0	0	0	0	1	0	0	0	0
1756	and	1	0	0	0	0	0	0	1	0	0	0
1756	as	1	0	0	1	0	0	0	0	0	0	0
1756	century	1	1	0	0	0	0	0	0	0	0	0
1756	godwin	1	0	0	0	0	1	0	0	0	0	0
1756	such	1	0	1	0	0	0	0	0	0	0	0
1756	weitling	1	0	0	0	0	0	0	0	0	1	0
1756	wilhelm	1	0	0	0	0	0	0	0	1	0	0
1756	william	1	0	0	0	1	0	0	0	0	0	0
1808	1756	1	1	0	0	0	0	0	0	0	0	0

although	common	1	0	0	0	1	0	0	0	0	0	0
although	consensus	1	0	0	0	0	1	0	0	0	0	0
although	contemporary	1	0	0	0	0	0	1	0	0	0	0
although	engage	1	1	0	0	0	0	0	0	0	0	0
although	explicitly	1	0	0	0	0	0	0	1	0	0	0
although	favours	1	0	0	0	0	0	0	0	1	0	0
although	few	1	0	0	0	0	0	1	0	0	0	0
although	governed	1	0	0	1	0	0	0	0	0	0	0
although	gradual	1	1	0	0	0	0	0	0	0	0	0
although	higher	1	0	0	0	0	0	0	0	0	0	1
although	highly	1	0	0	0	0	0	0	0	0	0	1
although	horizontalism	1	0	0	0	0	1	0	0	0	0	0
although	in	1	0	0	1	0	0	0	0	0	0	0
although	is	2	0	1	0	0	0	0	1	0	0	0
although	it	2	1	0	0	0	0	1	0	0	0	0
although	labelled	1	1	0	0	0	0	0	0	0	0	0
although	less	1	0	1	0	0	0	0	0	0	0	0
although	many	1	0	0	0	0	0	0	0	0	0	1
although	movement	1	0	0	0	0	1	0	0	0	0	0
although	not	1	0	0	0	0	0	1	0	0	0	0
although	on	1	0	0	0	1	0	0	0	0	0	0
although	opponents	1	0	0	1	0	0	0	0	0	0	0
although	or	1	1	0	0	0	0	0	0	0	0	0
although	over	1	0	0	0	0	0	0	0	0	0	1
although	overlap	1	0	0	0	0	0	0	0	0	1	0
although	personal	1	0	0	0	0	0	0	0	0	0	1
although	p

and	humanism	1	0	0	0	1	0	0	0	0	0	0
and	humans	3	2	0	0	0	0	0	0	1	0	0
and	i	2	0	0	1	0	0	0	0	0	1	0
and	ideal	3	0	0	0	1	1	0	0	0	0	1
and	idealistic	1	0	0	0	0	0	0	1	0	0	0
and	ideals	1	0	0	0	0	0	0	0	0	0	1
and	ideas	3	0	0	0	0	1	0	1	0	1	0
and	identity	1	0	0	0	0	1	0	0	0	0	0
and	ideological	1	0	0	0	0	0	0	0	0	1	0
and	ideologically	3	0	1	0	0	0	1	0	0	0	1
and	ideology	1	0	0	0	0	1	0	0	0	0	0
and	if	2	0	1	0	0	0	0	1	0	0	0
and	illegalism	1	0	0	0	0	1	0	0	0	0	0
and	illegitimate	1	0	0	0	0	0	0	0	0	0	1
and	illustrating	1	1	0	0	0	0	0	0	0	0	0
and	imperialism	1	0	0	0	0	0	1	0	0	0	0
and	implemented	1	0	0	0	0	0	0	0	0	1	0
and	important	2	1	0	0	0	0	0	0	0	0	1
and	in	47	3	7	3	6	0	1	8	7	6	6
and	inceptive	1	0	0	0	0	0	0	1	0	0	0
and	include	2	2	0	0	0	0	0	0	0	0	0
and	included	2	0	0	0	0	0	2	0	0	0	0
and	including	3	2	0	0	0	0	0	0	1	0	0
and	inconsistent	1	0	0	0	1	0	0	0	0	0	0
and	individual	5	0	0	0	1	3	1	0	0	0	0
and	individualism	3	0	0	0	1	1	1	0	0	0	0
and	individualist	5	0	0	1	0	1	1	0	1	1	0
and	individuality	2	0	0	0	0	1	1	0	0	0	0

authoritiy	inceptive	1	0	0	0	0	0	0	0	1	0	0
authoritiy	justified	1	0	0	0	0	1	0	0	0	0	0
authoritiy	network	1	1	0	0	0	0	0	0	0	0	0
authoritiy	organisation	1	0	1	0	0	0	0	0	0	0	0
authority	a	4	1	0	1	0	0	0	1	0	0	1
authority	acceptance	1	0	0	0	1	0	0	0	0	0	0
authority	acknowledging	1	0	0	0	0	1	0	0	0	0	0
authority	advantages	1	0	0	1	0	0	0	0	0	0	0
authority	against	1	0	0	0	1	0	0	0	0	0	0
authority	aim	1	0	1	0	0	0	0	0	0	0	0
authority	all	3	0	0	0	0	0	0	1	1	0	1
authority	also	1	0	0	0	0	0	1	0	0	0	0
authority	an	2	0	0	0	1	0	0	0	0	0	1
authority	anarchism	2	0	1	0	0	0	0	0	0	0	1
authority	anarchistic	1	0	0	0	0	0	0	0	0	1	0
authority	and	6	1	0	0	0	0	4	0	1	0	0
authority	another	1	0	0	0	0	0	0	0	0	0	1
authority	are	1	1	0	0	0	0	0	0	0	0	0
authority	argues	1	1	0	0	0	0	0	0	0	0	0
authority	articulated	1	0	0	0	0	0	0	0	1	0	0
authority	as	2	0	0	0	0	0	1	1	0	0	0
authority	autonomy	1	0	0	0	0	0	0	1	0	0	0
authority	be	1	1	0	0	0	0	0	0	0	0	0
authority	because	2	0	1	0	0	0	0	0	0	1	0
authority	belief	1	0	0	0	0	0	0	0	1	0	0
author

character	a	1	0	0	0	1	0	0	0	0	0	0
character	all	1	0	0	0	0	0	0	1	0	0	0
character	because	1	0	0	0	0	0	1	0	0	0	0
character	has	1	0	0	1	0	0	0	0	0	0	0
character	have	1	0	0	0	0	0	0	0	0	0	1
character	individuals	1	0	0	0	0	0	0	0	1	0	0
character	it	1	0	1	0	0	0	0	0	0	0	0
character	should	1	0	0	0	0	0	0	0	0	1	0
character	that	1	1	0	0	0	0	0	0	0	0	0
character	utopian	1	0	0	0	0	1	0	0	0	0	0
characterised	1840	1	0	0	1	0	0	0	0	0	0	0
characterised	a	1	0	0	0	0	0	0	0	0	1	0
characterised	as	2	0	0	0	0	0	1	0	1	0	0
characterised	been	1	0	0	0	1	0	0	0	0	0	0
characterised	between	1	0	0	0	0	0	0	0	0	1	0
characterised	first	1	0	0	0	0	1	0	0	0	0	0
characterised	goal	1	0	0	0	0	0	0	1	0	0	0
characterised	has	1	0	0	1	0	0	0	0	0	0	0
characterised	his	1	0	0	0	0	0	1	0	0	0	0
characterised	ideologically	1	0	0	0	0	0	0	1	0	0	0
characterised	individualist	1	0	0	0	0	0	0	0	0	0	1
characterised	is	1	1	0	0	0	0	0	0	0	0	0
characterised	mutualism	1	0	1	0	0	0	0	0	0	0	0
characterised	people	1	1	0	0	0	0	0	0	0	0	0
characterised	property	1	0	1

...

possible	along	1	0	0	0	0	0	0	0	1	0	0
possible	and	3	1	0	0	0	0	0	0	2	0	0
possible	any	1	0	0	0	1	0	0	0	0	0	0
possible	but	1	0	0	0	0	0	1	0	0	0	0
possible	by	1	0	0	1	0	0	0	0	0	0	0
possible	camouflaged	1	0	0	0	1	0	0	0	0	0	0
possible	capitalism	1	0	0	0	0	0	0	1	0	0	0
possible	coercion	1	0	0	1	0	0	0	0	0	0	0
possible	emma	1	0	0	0	0	0	1	0	0	0	0
possible	errico	1	0	0	0	0	0	0	0	0	1	0
possible	goldman	1	0	0	0	0	0	0	1	0	0	0
possible	if	2	0	0	0	0	1	0	0	0	0	1
possible	its	1	1	0	0	0	0	0	0	0	0	0
possible	justice	1	0	0	1	0	0	0	0	0	0	0
possible	malatesta	1	0	0	0	0	0	0	0	0	0	1
possible	means	2	1	0	0	0	1	0	0	0	0	0
possible	not	1	0	0	0	0	1	0	0	0	0	0
possible	of	1	0	1	0	0	0	0	0	0	0	0
possible	oppression	1	0	1	0	0	0	0	0	0	0	0
possible	other	1	0	0	0	0	0	0	0	0	0	1
possible	overt	1	0	0	0	0	0	0	0	0	1	0
possible	social	1	0	1	0	0	0	0	0	0	0	0
possible	unceremonious	1	0	0	0	0	0	0	1	0	0	0
possible	under	1	0	0	0	0	0	1	0	0	0	0
possible	were	1	0	0	0	1	0	0	0	0	0	0
possible	with	1	0	0	0	0	0	0	0	0	1	0
post	19th	1	0	1	0	0	0	0

say	an	1	0	0	0	0	0	0	0	0	1	0
say	anarchism	1	0	0	0	0	0	0	1	0	0	0
say	approach	1	0	0	0	0	0	0	0	0	0	1
say	be	1	0	0	1	0	0	0	0	0	0	0
say	cluster	1	0	0	0	0	0	0	0	0	0	1
say	decision	1	0	0	0	0	0	0	0	1	0	0
say	each	1	0	0	0	0	0	0	1	0	0	0
say	equal	1	0	0	0	0	1	0	0	0	0	0
say	everyone	1	0	0	1	0	0	0	0	0	0	0
say	having	1	0	0	0	1	0	0	0	0	0	0
say	in	1	0	0	0	0	0	1	0	0	0	0
say	is	1	0	0	0	0	0	0	0	1	0	0
say	it	1	1	0	0	0	0	0	0	0	0	0
say	might	1	0	1	0	0	0	0	0	0	0	0
say	that	1	0	0	0	0	0	1	0	0	0	0
say	to	1	0	0	0	0	1	0	0	0	0	0
say	true	1	0	0	0	1	0	0	0	0	0	0
say	way	1	1	0	0	0	0	0	0	0	0	0
say	with	1	0	1	0	0	0	0	0	0	0	0
scenes	anarchists	1	0	0	0	0	0	0	0	0	1	0
scenes	as	1	0	0	0	0	0	0	1	0	0	0
scenes	associated	1	0	0	1	0	0	0	0	0	0	0
scenes	been	1	0	1	0	0	0	0	0	0	0	0
scenes	has	1	1	0	0	0	0	0	0	0	0	0
scenes	music	1	0	0	0	0	1	0	0	0	0	0
scenes	punk	1	0	0	0	0	0	0	0	1	0	0
scenes	such	2	0	0	0	0	0	1	0	0	0	1
scenes	with	1	0	0	0	1	0	0	0	0	0	0
sceptical	all	1	0	0	0	0	0	0	0	0	0	1
sceptical	and	2	0	1	0	0	0	0	0	1	0	0
sceptical	au

such	william	2	0	0	0	0	0	0	2	0	0	0
such	wing	1	0	1	0	0	0	0	0	0	0	0
such	with	3	0	0	1	1	0	0	0	0	0	1
such	writers	1	0	0	0	0	1	0	0	0	0	0
such	wrote	1	0	0	0	0	0	0	0	1	0	0
suffix	current	1	0	0	0	0	0	0	0	0	0	1
suffix	denotes	1	0	0	0	0	0	0	1	0	0	0
suffix	e	1	1	0	0	0	0	0	0	0	0	0
suffix	ideological	1	0	0	0	0	0	0	0	0	1	0
suffix	ism	1	0	0	0	0	0	1	0	0	0	0
suffix	leader	1	0	1	0	0	0	0	0	0	0	0
suffix	or	1	0	0	1	0	0	0	0	0	0	0
suffix	ruler	1	0	0	0	1	0	0	0	0	0	0
suffix	the	2	0	0	0	0	1	0	0	1	0	0
suffrage	anarchist	1	0	1	0	0	0	0	0	0	0	0
suffrage	but	1	0	0	0	0	0	1	0	0	0	0
suffrage	differed	1	0	0	0	1	0	0	0	0	0	0
suffrage	feminists	1	0	0	1	0	0	0	0	0	0	0
suffrage	non	1	1	0	0	0	0	0	0	0	0	0
suffrage	nonetheless	1	0	0	0	0	0	0	0	0	1	0
suffrage	on	1	0	0	0	0	1	0	0	0	0	0
suffrage	supportive	1	0	0	0	0	0	0	0	0	0	1
suffrage	they	1	0	0	0	0	0	0	1	0	0	0
suffrage	were	1	0	0	0	0	0	0	0	1	0	0
suggesting	a	1	0	0	0	0	0	1	0	0	0	0
suggesting	an	1	0	0	0	0	0	0	0	0	0	1
suggesting	feminist	1	0	0	0	1	0	0	0	0	0	0
suggesting	from	1	1	0	

theory	anarcho	1	0	1	0	0	0	0	0	0	0	0
theory	and	2	1	0	0	0	0	0	0	0	0	1
theory	at	1	0	0	0	0	0	1	0	0	0	0
theory	belief	1	0	0	0	0	0	0	0	0	1	0
theory	bitter	1	0	1	0	0	0	0	0	0	0	0
theory	by	1	0	0	0	0	0	1	0	0	0	0
theory	capitalism	1	0	0	0	0	0	0	0	0	1	0
theory	century	1	0	0	0	1	0	0	0	0	0	0
theory	communism	1	0	0	1	0	0	0	0	0	0	0
theory	compatibility	1	0	0	0	0	0	0	1	0	0	0
theory	concerns	1	0	0	1	0	0	0	0	0	0	0
theory	criticism	1	0	0	0	0	0	0	0	0	0	1
theory	debates	1	0	0	1	0	0	0	0	0	0	0
theory	definitional	1	0	1	0	0	0	0	0	0	0	0
theory	developed	2	0	0	1	0	0	0	0	1	0	0
theory	economic	1	0	0	0	0	1	0	0	0	0	0
theory	favours	1	0	1	0	0	0	0	0	0	0	0
theory	fertile	1	0	0	0	0	0	0	0	0	1	0
theory	found	1	0	0	0	0	0	0	0	1	0	0
theory	groups	1	0	0	0	0	0	0	0	1	0	0
theory	in	3	0	0	0	1	0	1	0	0	0	1
theory	into	3	0	1	0	1	0	0	0	0	1	0
theory	is	2	1	0	0	1	0	0	0	0	0	0
theory	its	1	0	0	0	0	0	0	0	0	0	1
theory	joseph	2	0	0	1	0	0	0	0	1	0	0
theory	line	1	0	0	0	0	0	0	0	1	0	0
theory	mutualism	1	0	0	0	0	0	0	1	0	0	0
theory	nationalis

view	a	1	0	0	0	0	0	0	1	0	0	0
view	according	1	0	1	0	0	0	0	0	0	0	0
view	anarchists	1	0	0	0	0	0	0	1	0	0	0
view	become	1	0	0	1	0	0	0	0	0	0	0
view	by	1	0	0	0	0	0	0	0	1	0	0
view	dominating	1	0	0	0	0	1	0	0	0	0	0
view	go	1	1	0	0	0	0	0	0	0	0	0
view	idea	1	0	0	0	0	0	0	0	0	1	0
view	late	1	0	0	0	0	0	0	0	0	0	1
view	marxist	1	0	0	0	0	1	0	0	0	0	0
view	of	1	0	0	0	0	0	1	0	0	0	0
view	onto	1	0	1	0	0	0	0	0	0	0	0
view	social	1	0	0	0	0	0	0	0	1	0	0
view	that	1	0	0	0	0	0	1	0	0	0	0
view	the	3	0	0	0	2	0	0	0	0	1	0
view	to	1	0	0	1	0	0	0	0	0	0	0
view	values	1	1	0	0	0	0	0	0	0	0	0
view	would	1	0	0	0	0	0	0	0	0	0	1
views	a	2	1	0	0	0	0	0	0	0	1	0
views	according	1	0	0	0	0	0	0	0	1	0	0
views	accused	1	0	0	1	0	0	0	0	0	0	0
views	all	1	1	0	0	0	0	0	0	0	0	0
views	anarchism	1	0	0	0	1	0	0	0	0	0	0
views	anarchist	1	0	0	0	0	1	0	0	0	0	0
views	anarchists	1	0	0	0	0	0	0	0	1	0	0
views	and	1	0	0	0	0	0	1	0	0	0	0
views	as	1	0	0	0	0	0	0	0	1	0	0
views	branch	1	0	1	0	0	0	0	0	0	0	0
views	few	1	1	0	0	0	0	0	0	0	0	0
views	have	1	0	0	0	1	0	0	0	0

### Step 4: Combine them together!  

Now you can move your code above into mapper.py and reducer.py (with some tiny modifications, of course), and this is your assignment this week!   
See below for detailed requirement description.  

**Hints: What should I modify in my mapper and reducer?**  

1. Receive/pass data from standard I/O, rather than the file (We've already done this for you)
2. Process with the whole dataset, rather than only the first line

That's it!  

The processing takes some times (~1hr w/o parallel computing), so go enjoy some coffee or movies (or sleep) during the waiting time ;)

<a name="Assignment-Requirement"></a>
## Assignment Requirement 

1. You need to implement the `mapper.py` and `reducer.py` to calculate the skip-gram table.

2. In `mapper.py`, you need to generate skipgrams with distance within -5 to 5 (inclusive).  
   - Input: Pure text file (`wiki1G.txt`) with each line as a wikipage.
   - Output: `"{pivot}\t{word}\t{distance}\t{count}"`
   - Example: 
     ```
     predict is  -3  1
     predict used    -2  1
     predict the -1  1
     predict the 1   1
     ...
     ```
   - Sample output: `mapper.sample.tsv` (Find it [here](https://drive.google.com/drive/folders/1vKxr--sLd2J4kdsXUzJDBZdG3AmV4NGl?usp=sharing); no need to be exactly the same)

3. In `reducer.py`, you have to collect the output from the shuffler (`sort`) and generate the skip-gram table.
   - Input: `"{pivot}\t{word}\t{distance}\t{count}"`
   - Output: 
     - `"{pivot}\t{word}\t{total}\t{-5}\t{-4}\t{-3}\t{-2}\t{-1}\t{1}\t{2}\t{3}\t{4}\t{5}"`
     - The first two column are the skipgram; the third column is the sum of total frequency; column 4\~13 are the frequency with distance -5\~5, without 0.
   - Example:
     ```
     arouse  of      1       0       0       0       0       0       0       0       1       0       0
     arouse  open    4       0       0       3       0       0       0       0       0       0       1
     arouse  so      2       0       1       0       0       0       0       0       0       1       0
     arouse  sufficiently    1       0       1       0       0       0       0       0       0       0       0
     ...
     ```
   - Sample output: `reducer.sample.tsv` (Find it [here](https://drive.google.com/drive/folders/1vKxr--sLd2J4kdsXUzJDBZdG3AmV4NGl?usp=sharing); no need to be exactly the same)

4. Concate your MapReduce procedure and generate the skip-gram on wiki1G dataset
   - Unix: 
     - Use the [local map-reduce tool](https://github.com/dspp779/local-mapreduce) (faster),
     - or run it directly: `python mapper.py < wiki1G.txt | sort -k1,2 -k3n | python reducer.py > skipgram.tsv` (slower)
   - Windows: 
     - CMD: `python mapper.py < wiki1G.txt | sort | python reducer.py > skipgram.tsv`
     - PS: `type wiki1G.txt | python mapper.py | sort | python reducer.py > skipgram.tsv`
     - or the bash environment you installed last week.  
   - See [Appendix](#built-in-command) if you want to know what these commands mean

During the demo, you need to 

1. show us your skip-gram result on the given dataset, and
2. explain your implementation in `mapper.py` and `reducer.py`.  

Note that the final result would be a large file (~6 GB), so **you may want to show it with `more` or `less` command**.  

## TA's note

Congratulations! You've learned how to calculate skipgram frequency and to deal with a huge dataset with MapReduce technique.  

Remember to <b><a href="https://docs.google.com/spreadsheets/d/1QGeYl5dsD9sFO9SYg4DIKk-xr-yGjRDOOLKZqCLDv2E/edit?usp=sharing">make an appoiment with TA</a> to demo/explain your implementation <u>before <font color="red">10/21 15:30</font></u></b> .  
You should also submit your `mapper.py` and `reducer.py` to <a href="https://eeclass.nthu.edu.tw/course/homework/3285">eeclass</a> .

<a name="built-in-command"></a>
## Appendix: useful built-in commands

Several built-in commands are very useful in the MapReducer procedure.  
Here we introduce `cat` and `type`, `<` and `>`, `sort`, and pipe `|`.  

### cat (on Unix)
`cat` command, which is definitly not indicating some cute creatures (*meow~*), is the abbreviation of `concatenate`. ([doc](https://man7.org/linux/man-pages/man1/cat.1.html))   

When you `cat` a file, it means you want to print the content from a file (or some files) to standard output.  
Now open your bash and test the command below!  
```bash
cat file.txt
```

You should see something like this: 

![picture](https://i.imgur.com/Z9shOYQ.png)

### type (on Windows)
`type` command works exactly the same as `cat` on Unix, but without its cute nickname (Shame on you, Windows). ([doc](https://docs.microsoft.com/en-us/windows-server/administration/windows-commands/type))  

Similarly, if you `type` a file, it means you print the content from a file (or some files) to standard output.  

```powershell
type file.txt
```

You should see something like this:  
![](https://i.imgur.com/5WFhxkq.png)

### `>`? `<`? `>///<`? 

`<` and `>` are the I/O redirections.  
`program < filename` means that you want to redirect the input from a file to a program, while `program > filename` means that you want to redirect the output of a program to that file.  

For example,
```bash
echo "hello world" > greet.txt
```
writes the string "hello world" into a file `greet.txt`.  

On the other hand, 
```bash
head < greet.txt
```
makes `head` receive the content from `greet.txt`, so it will print out the string in `greet.txt`.  
![](https://i.imgur.com/swxv8LG.png)
<small>p.s. `>///<` is just a joke. Don't take it seriously.</small>

### sort

As its name suggests, `sort` sorts the data that it receives. (doc on [Linux](https://man7.org/linux/man-pages/man1/sort.1.html) and on [Windows](https://docs.microsoft.com/en-us/windows-server/administration/windows-commands/sort))  
Try this:
```
sort sample.txt
```
You can see that the content has been sorted before printed onto your screen.  
![](https://i.imgur.com/QFEq3Tc.png)

### Pipe `|`

Pipe passes the output from previous program to the next program.  
For example, 
```bash
python program.py | sort
```
will pass the output of `program.py` to `sort` command.  